<a href="https://colab.research.google.com/github/Adiaslow/PepLab/blob/main/Unique_Mass_Genetic_Library_Generator.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Unique Mass Genetic Library Generator
---

This genetic algorithm is designed to optimize split pool schemes for peptide synthesis such that every member of the library has a unique mass relative, a unique mass + mass of hydrogen, and a unique mass + mass of sodium.

This implementation is a proof of concept and would have implementations for removing the mass of water, options for linear or cyclized, and other features to make the final masses more accurate.

## Overview

1. **Initialization**: The algorithm starts by creating an initial population of random split pool schemes.
2. **Fitness Evaluation**: Each scheme in the population is evaluated based on its fitness, which considers factors like mass uniqueness, peptide diversity, and the number of peptides produced.
3. **Selection**: The best-performing schemes are selected to become parents for the next generation.
4. **Crossover**: Parent schemes are combined to create new offspring schemes.
5. **Mutation**: Random changes are introduced to some schemes to maintain diversity in the population.
6. **Iteration**: Steps 2-5 are repeated for a specified number of generations or until a stopping criterion is met.
7. **Adaptation**: The algorithm adapts its parameters over time based on the population's performance.

## Parameters

| Parameter | Description |
| - | - |
| population_size | The number of split pool schemes in each generation. A larger population increases diversity but also increases computation time. |
| number_of_residues | The number of steps in each split pool scheme. This determines the length of the peptides produced. |
| mutation_rate | The probability of a mutation occurring in each step of a scheme during reproduction. Higher rates increase diversity but may slow convergence. |
| number_of_generations | The maximum number of iterations the algorithm will run. More generations allow for more optimization but increase computation time. |
| initial_min_aa | The minimum number of amino acids allowed in each step at the start of the algorithm. |
| initial_max_aa | The maximum number of amino acids allowed in each step at the start of the algorithm. |
| max_aa | The absolute maximum number of amino acids allowed in each step. This caps the adaptive range. |
| optimal_fitness_threshold | The fitness score above which a scheme is considered optimal. Perfect fitness is 1.0. |
| early_stop | The number of generations without improvement after which the algorithm will terminate early. This prevents unnecessary computation if the algorithm has converged. |
| mass_threshold | The minimum mass difference required between peptides for them to be considered distinct. This affects the uniqueness score in fitness calculation. |
| h_mass | The mass of a hydrogen ion (H$^+$). Used in calculating adduct masses for fitness evaluation. |
| na_mass | The mass of a sodium ion (Na$^+$). Used in calculating adduct masses for fitness evaluation. |

These parameters allow fine-tuning of the algorithm's behavior to optimize performance for specific peptide synthesis scenarios.

---
## Into the Weeds

### 1. Initialization
The algorithm begins by creating an initial population of random split pool schemes. Each scheme is represented as a `SplitPoolScheme` object, which contains a sequence of steps. Each step is a collection of amino acids.

- The number of steps is determined by `number_of_residues`.
- The number of amino acids in each step is randomly chosen between `initial_min_aa` and `initial_max_aa`.
- The total number of schemes created is equal to `population_size`.

### 2. Fitness Evaluation
For each scheme in the population, a fitness score is calculated. This score represents how well the scheme meets the desired criteria for peptide synthesis. The fitness calculation involves several components:
 - Mass Calculation: The algorithm calculates the masses of all possible peptides that could be produced by the scheme, including potential H$^+$ and Na$^+$ adducts.
 - Uniqueness Score: This measures how many unique peptide masses the scheme produces relative to the total number of peptides.
 - Mass Differentiation Score: This evaluates how well-separated the peptide masses are. It counts how many pairs of masses are closer than `mass_threshold` and penalizes the score accordingly.
 - Amino Acid Diversity Score: This rewards schemes that use a diverse set of amino acids in each step.

 These components are weighted and combined to produce a final fitness score between 0 and 1, where 1 is perfect fitness.

### 3. Selection
The algorithm uses tournament selection to choose parent schemes for the next generation:

 - For each new offspring to be created, three schemes are randomly selected from the population.
 - The scheme with the highest fitness among these three becomes a parent.
 - This process is repeated to select the second parent.

### 4. Crossover

Crossover combines genetic material from two parent schemes to create new offspring:

 - A random crossover point is chosen.
 - The first part of the sequence from one parent is combined with the second part from the other parent to create a new scheme.
 - This process creates two new offspring from each pair of parents.

5. Mutation

After crossover, each new scheme has a chance to mutate. For each step in the scheme:

There's a `mutation_rate` chance of mutation occurring.
If mutation occurs, one of three actions is randomly chosen:

 - **Add**: A new random amino acid is added to the step (if below `max_aa`).
 - **Remove**: A random amino acid is removed from the step (if above the current minimum).
 - **Replace**: A random amino acid in the step is replaced with a different random amino acid.

### 6. Iteration and Adaptive Parameters
The algorithm repeats steps 2-5 for `number_of_generations` iterations, with some additional features:

 - **Elitism**: The best scheme from each generation is automatically carried over to the next generation unchanged.
 - **Adaptive Parameters**: The algorithm adjusts `min_aa` and `max_aa` based on the population's performance:

If all schemes with the minimum number of amino acids per step have perfect fitness, min_aa is increased.

If more than half of the schemes with the maximum number of amino acids per step have near-perfect fitness, `max_aa` is increased (up to `max_aa`).

### 7. Termination and Results
The algorithm can terminate in two ways:

1. It reaches `number_of_generations` iterations.
2. It triggers an early stop if there's no improvement in the best fitness for `early_stop` consecutive generations.

Upon termination, the algorithm returns:

- A list of all schemes that achieved fitness greater than or equal to `optimal_fitness_threshold`.
- The overall best scheme found during the entire run.
- The fitness score and number of peptides for the best scheme.

### Additional Considerations

- **Caching**: The algorithm uses caching strategies to avoid recalculating masses for schemes that haven't changed, improving efficiency.
- **Parallelization**: While not implemented in this version, the algorithm's structure allows for potential parallelization of fitness calculations and genetic operations.
- **Balance**: The parameters allow for fine-tuning the balance between exploration (finding diverse solutions) and exploitation (optimizing good solutions). For example, higher `mutation_rate` and `population_size` promote exploration, while a higher `optimal_fitness_threshold` and lower `early_stop` promote exploitation.

This genetic algorithm combines elements of natural selection, genetic recombination, and mutation to efficiently search the vast space of possible split pool schemes, converging on optimal solutions for mass differentiated peptide libraries.

# Setup

In [ ]:
# @title Install Packages
_ = !pip install rdkit-pypi
_ = !pip install -q pydot


In [ ]:
# @title Install Modules

import cmath
from collections import defaultdict
import csv
from dataclasses import dataclass
from functools import lru_cache, reduce
from google.colab import files
from itertools import product
import matplotlib.pyplot as plt
import math
from math import pi, cos, sin
from multiprocessing import Pool, cpu_count
# from networkx.drawing.nx_pydot import graphviz_layout
from networkx.drawing.nx_agraph import graphviz_layout
from numba import jit, vectorize
import numpy as np
from operator import mul
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
import networkx as nx
import random
from rdkit import Chem
from rdkit.Chem import AllChem
from rdkit.Chem import Draw
from rdkit.Chem import Descriptors
import re
import requests
from tqdm.notebook import tqdm
from typing import List, Tuple, FrozenSet, Dict, Optional


# Load Data

In [ ]:
# @title Load side chains
# @markdown Click "Choose Files" and select `swiss_sidechain.csv`.
uploaded = files.upload()
file_path = list(uploaded.keys())[0]
sidechains = pd.read_csv(file_path)
display(sidechains)

Saving swiss_sidechain.csv to swiss_sidechain.csv


id_d_form                   full_name  \
0         ALA                     Alanine   
1         ARG                    Arginine   
2         ASN                  Asparagine   
3         ASP               Aspartic Acid   
4         CYS                    Cysteine   
..        ...                         ...   
245       VAH            Hydroxynorvaline   
246       VAL                      Valine   
247       WFP  3,5-Difluoro-phenylalanine   
248       YCM        cysteine-s-acetamide   
249       YOF            3-fluorotyrosine   

                                              smi_href        mass  \
0                                                  NaN   71.078059   
1                                                  NaN  156.186082   
2                                                  NaN  114.102884   
3                                                  NaN  115.087605   
4                                                  NaN  103.144144   
..                                                 ...         ...   
245  https://www.swisssidechain.ch/data/sidechain/V...  126.091000   
246  https://www.swisssidechain.ch/data/sidechain/V...  109.084000   
247  https://www.swisssidechain.ch/data/sidechain/W...  111.047000   
248  https://www.swisssidechain.ch/data/sidechain/Y...  171.155000   
249  https://www.swisssidechain.ch/data/sidechain/Y...  108.048000   

    calc_method                             smiles Unnamed: 6  
0           NaN                                NaN     C3H5NO  
1           NaN                                NaN   C6H12N4O  
2           NaN                                NaN   C4H6N2O2  
3           NaN                                NaN    C4H5NO3  
4           NaN                                NaN    C3H5NOS  
..          ...                                ...        ...  
245         NaN   CC[C@H]([C@@H]([C](=O)=O)[NH2])O        NaN  
246         NaN           [NH2][C@@H](C(C)C)C(=O)O        NaN  
247         NaN  [NH2][C@H](C(=O)O)Cc1cc(F)cc(c1)F        NaN  
248         NaN       NC(=O)CSC[C@@H](C(=O)O)[NH2]        NaN  
249         NaN  OC(=O)[C@H](Cc1ccc(c(c1)F)O)[NH2]        NaN  

[250 rows x 7 columns]

# Genetic Algorithm for Unique Mass Library Design

In [ ]:
# @title Genetic Algorithm
# @markdown Genetic Algorithm for Split Pool Scheme Optimization.

population_size = 20 # @param {type:"number"}
number_of_residues = 5 # @param {type:"number"}
mutation_rate = 0.05 # @param {type:"number"}
number_of_generations = 100 # @param {type:"number"}
initial_min_aa = 5 # @param {type:"number"}
initial_max_aa = 10 # @param {type:"number"}
max_aa = 20 # @param {type:"number"}
optimal_fitness_threshold = 0.9999 # @param {type:"number"}
early_stop = 1000 # @param {type:"number"}
mass_threshold = 0.5 # @param {type:"number"}
h_mass = 1.008 # @param {type:"number"}
na_mass = 22.989 # @param {type:"number"}

@dataclass(frozen=True)
class AminoAcid:
    """Represents an amino acid with its properties."""
    name: str
    mass: float
    is_d: bool = False

@dataclass
class SplitPoolScheme:
    """Represents a split pool scheme for peptide synthesis."""
    steps: Tuple[Tuple[AminoAcid, ...], ...]

    def __post_init__(self):
        self._cached_masses = None
        self._cached_peptide_count = None

    @property
    def masses(self) -> np.ndarray:
        """Calculate and cache the masses of all possible peptides."""
        if self._cached_masses is None:
            self._cached_masses = self._calculate_masses()
        return self._cached_masses

    @property
    def peptide_count(self) -> int:
        """Calculate and cache the total number of possible peptides."""
        if self._cached_peptide_count is None:
            self._cached_peptide_count = np.prod([len(step) for step in self.steps])
        return self._cached_peptide_count

    def _calculate_masses(self) -> np.ndarray:
        """Calculate the masses of all possible peptides."""
        return np.array([sum(aa.mass for aa in peptide)
                         for peptide in self._generate_all_peptides()])

    def _generate_all_peptides(self) -> List[Tuple[AminoAcid, ...]]:
        """Generate all possible peptide combinations."""
        peptides = [()]
        for step in self.steps:
            peptides = [peptide + (aa,) for peptide in peptides for aa in step]
        return peptides

    @property
    def avg_aa_per_step(self) -> float:
        """Calculate the average number of amino acids per step."""
        return sum(len(step) for step in self.steps) / len(self.steps)


class AdaptiveParameters:
    """Manages adaptive parameters for the genetic algorithm."""

    def __init__(self, initial_min: int, initial_max: int, max_possible: int):
        self.min_aa = initial_min
        self.max_aa = initial_max
        self.max_possible = max_possible
        self.perfect_fitness_counts = defaultdict(int)
        self.total_counts = defaultdict(int)

    def update(self, schemes: List[SplitPoolScheme], fitnesses: List[float]) -> None:
        """Update parameters based on current population performance."""
        for scheme, fitness in zip(schemes, fitnesses):
            aa_count = round(scheme.avg_aa_per_step)
            self.total_counts[aa_count] += 1
            if fitness >= 0.99:  # Consider near-perfect fitness
                self.perfect_fitness_counts[aa_count] += 1

        if (self.perfect_fitness_counts[self.min_aa] == self.total_counts[self.min_aa]
            and self.total_counts[self.min_aa] > 0):
            self.min_aa = min(self.min_aa + 1, self.max_possible - 1)

        if (self.perfect_fitness_counts[self.max_aa] > self.total_counts[self.max_aa] / 2
            and self.total_counts[self.max_aa] > 0):
            self.max_aa = min(self.max_aa + 1, self.max_possible)

    def get_aa_range(self) -> Tuple[int, int]:
        """Get the current range of amino acids per step."""
        return self.min_aa, self.max_aa


class FitnessCalculator:
    """Calculates fitness for SplitPoolSchemes."""

    def __init__(self, threshold: float, h_mass: float, na_mass: float):
        self.threshold = threshold
        self.h_mass = h_mass
        self.na_mass = na_mass

    def calculate(self, scheme: SplitPoolScheme) -> Tuple[float, int]:
        """Calculate the fitness of a given SplitPoolScheme."""
        masses = scheme.masses
        total_masses = len(masses)

        if total_masses == 1:
            return (1.0, 1)  # Perfect fitness for a single peptide

        # Create arrays for H+ and Na+ adducts
        h_adducts = masses + self.h_mass
        na_adducts = masses + self.na_mass

        # Combine all masses and adducts
        all_masses = np.concatenate([masses, h_adducts, na_adducts])

        # Sort the masses for efficient comparison
        sorted_masses = np.sort(all_masses)

        # Calculate mass differences
        mass_diffs = np.diff(sorted_masses)

        # Count violations (masses closer than the threshold)
        violations = np.sum(mass_diffs < self.threshold)

        # Calculate uniqueness score
        uniqueness_score = len(np.unique(masses)) / total_masses

        # Calculate mass differentiation score
        total_comparisons = len(all_masses) * (len(all_masses) - 1) // 2
        mass_diff_score = 1 - (violations / total_comparisons) if total_comparisons > 0 else 1

        # Calculate amino acid diversity score
        aa_diversity_score = min(scheme.avg_aa_per_step / 7, 1)

        # Combine scores
        w1, w2, w3 = 0.4, 0.4, 0.2
        fitness_score = w1 * uniqueness_score + w2 * mass_diff_score + w3 * aa_diversity_score

        return (min(max(fitness_score, 0), 1), total_masses)


class GeneticOperator:
    """Performs genetic operations on SplitPoolSchemes."""

    def __init__(self, amino_acids: Tuple[AminoAcid, ...], mutation_rate: float):
        self.amino_acids = amino_acids
        self.mutation_rate = mutation_rate

    def crossover(self, parent1: SplitPoolScheme, parent2: SplitPoolScheme) -> Tuple[SplitPoolScheme, SplitPoolScheme]:
        """Perform crossover between two parent schemes."""
        split = random.randint(1, len(parent1.steps) - 1)
        child1 = SplitPoolScheme(parent1.steps[:split] + parent2.steps[split:])
        child2 = SplitPoolScheme(parent2.steps[:split] + parent1.steps[split:])
        return child1, child2

    def mutate(self, scheme: SplitPoolScheme, min_aa: int, max_aa: int) -> SplitPoolScheme:
        """Mutate a given scheme."""
        new_steps = list(scheme.steps)
        for i, step in enumerate(new_steps):
            if random.random() < self.mutation_rate:
                action = random.choices(['add', 'remove', 'replace'], weights=[0.4, 0.3, 0.3])[0]
                step = list(step)
                if action == 'add' and len(step) < max_aa:
                    step.append(random.choice(self.amino_acids))
                elif action == 'remove' and len(step) > min_aa:
                    step.pop(random.randint(0, len(step) - 1))
                elif action == 'replace':
                    step[random.randint(0, len(step) - 1)] = random.choice(self.amino_acids)
                new_steps[i] = tuple(step)
        return SplitPoolScheme(tuple(new_steps))

class GeneticAlgorithm:
    """Implements the genetic algorithm for optimizing SplitPoolSchemes."""

    def __init__(self, config: Dict):
        self.pop_size = config['pop_size']
        self.n_steps = config['n_steps']
        self.generations = config['generations']
        self.early_stop = config['early_stop']
        self.optimal_fitness_threshold = config['optimal_fitness_threshold']

        self.amino_acids = tuple(config['amino_acids'])
        self.adaptive_params = AdaptiveParameters(
            config['initial_min_aa'],
            config['initial_max_aa'],
            config['max_aa']
        )
        self.fitness_calculator = FitnessCalculator(
            config['mass_threshold'],
            config['h_mass'],
            config['na_mass']
        )
        self.genetic_operator = GeneticOperator(
            self.amino_acids,
            config['mutation_rate']
        )

    def initialize_population(self) -> List[SplitPoolScheme]:
        """Initialize the population with random schemes."""
        return [self._create_random_scheme() for _ in range(self.pop_size)]

    def _create_random_scheme(self) -> SplitPoolScheme:
        """Create a random SplitPoolScheme."""
        min_aa, max_aa = self.adaptive_params.get_aa_range()
        return SplitPoolScheme(tuple(
            tuple(random.sample(self.amino_acids, random.randint(min_aa, max_aa)))
            for _ in range(self.n_steps)
        ))

    def run(self) -> Tuple[List[SplitPoolScheme], SplitPoolScheme, Tuple[float, int]]:
        """Run the genetic algorithm."""
        population = self.initialize_population()
        best_fitness = (0, 0)
        best_scheme = None
        optimal_schemes = []
        generations_without_improvement = 0

        with tqdm(total=self.generations, desc="Genetic Algorithm Progress") as pbar:
            for _ in range(self.generations):
                fitnesses = [self.fitness_calculator.calculate(scheme)[0] for scheme in population]

                self.adaptive_params.update(population, fitnesses)

                current_best = max(zip(population, fitnesses), key=lambda x: x[1])
                current_best_scheme, current_best_fitness = current_best

                if (current_best_fitness, current_best_scheme.peptide_count) > best_fitness:
                    best_fitness = (current_best_fitness, current_best_scheme.peptide_count)
                    best_scheme = current_best_scheme
                    generations_without_improvement = 0
                else:
                    generations_without_improvement += 1

                optimal_schemes = [scheme for scheme, fit in zip(population, fitnesses) if fit >= self.optimal_fitness_threshold]

                elite_scheme = current_best_scheme

                parents = [max(random.sample(list(enumerate(fitnesses)), 3), key=lambda x: x[1])[0] for _ in range(self.pop_size - 1)]

                next_gen = [elite_scheme]
                for i in range(0, len(parents), 2):
                    if i + 1 < len(parents):
                        child1, child2 = self.genetic_operator.crossover(population[parents[i]], population[parents[i+1]])
                        min_aa, max_aa = self.adaptive_params.get_aa_range()
                        next_gen.extend([
                            self.genetic_operator.mutate(child1, min_aa, max_aa),
                            self.genetic_operator.mutate(child2, min_aa, max_aa)
                        ])

                population = next_gen

                pbar.set_postfix({
                    'Best Fitness': f'{best_fitness[0]:.4f}',
                    'Best Peptides': best_fitness[1],
                    'Optimal Schemes': len(optimal_schemes),
                    'AA Range': f'{self.adaptive_params.min_aa}-{self.adaptive_params.max_aa}'
                })
                pbar.update(1)

                if generations_without_improvement >= self.early_stop:
                    print(f"\nEarly stopping after {generations_without_improvement} generations without improvement.")
                    break

        sorted_optimal_schemes = sorted(optimal_schemes, key=lambda x: (self.fitness_calculator.calculate(x)[0], x.peptide_count), reverse=True)
        return sorted_optimal_schemes, best_scheme, best_fitness


def run_genetic_algorithm(config: Dict) -> Tuple[List[SplitPoolScheme], SplitPoolScheme, Tuple[float, int]]:
    """Run the genetic algorithm with the given configuration."""
    ga = GeneticAlgorithm(config)
    optimal_schemes, best_scheme, best_fitness = ga.run()

    print(f"\nBest overall fitness: {best_fitness[0]:.4f}")
    print(f"Number of peptides in best scheme: {best_fitness[1]}")
    print(f"\nNumber of optimal schemes found: {len(optimal_schemes)}")

    print("\nBest overall scheme:")
    for j, step in enumerate(best_scheme.steps):
        print(f"  Step {j+1}: {[aa.name for aa in step]}")
    print(f"  Fitness: {best_fitness[0]:.4f}")
    print(f"  Total number of peptides: {len(best_scheme.masses)}")
    print(f"  Number of unique masses: {len(np.unique(best_scheme.masses))}")

    if optimal_schemes:
        print("\nTop 5 optimal schemes:")
        for i, scheme in enumerate(optimal_schemes[:5], 1):
            print(f"\nScheme {i}:")
            for j, step in enumerate(scheme.steps):
                print(f"  Step {j+1}: {[aa.name for aa in step]}")
            scheme_fitness = ga.fitness_calculator.calculate(scheme)[0]
            print(f"  Fitness: {scheme_fitness:.4f}")
            print(f"  Total number of peptides: {len(scheme.masses)}")
            print(f"  Number of unique masses: {len(np.unique(scheme.masses))}")

        if len(optimal_schemes) > 5:
            print("\n... (remaining schemes omitted for brevity)")
    else:
        print("\nNo optimal schemes found.")

    return optimal_schemes, best_scheme, best_fitness

config = {
    'pop_size': population_size,
    'n_steps': number_of_residues,
    'generations': number_of_generations,
    'early_stop': early_stop,
    'mutation_rate': mutation_rate,
    'mass_threshold': mass_threshold,
    'h_mass': h_mass,
    'na_mass': na_mass,
    'optimal_fitness_threshold': optimal_fitness_threshold,
    'initial_min_aa': initial_min_aa,
    'initial_max_aa': initial_max_aa,
    'max_aa': max_aa,
    'amino_acids': [AminoAcid(name=row['id_d_form'], mass=row['mass']) for _, row in sidechains.iterrows()]
}

optimal_schemes, best_scheme, best_fitness = run_genetic_algorithm(config)

Genetic Algorithm Progress:   0%|          | 0/100 [00:00<?, ?it/s]


Best overall fitness: 1.0000
Number of peptides in best scheme: 16800

Number of optimal schemes found: 15

Best overall scheme:
  Step 1: ['FVAL', 'TFG4', 'ABA', 'BIU', 'CTE', 'ACZ', 'AHB']
  Step 2: ['TYR', 'PHE', '4IN', 'HLU', '0BN', 'ASN', 'THR', 'Sep2', 'TYI', 'GLY']
  Step 3: ['NIY', 'BIF', 'MET', 'SER', 'THR', 'ARG']
  Step 4: ['CPH2', 'LEU', 'GGB', '2FM', 'MET']
  Step 5: ['CP24', 'PHI', 'DILE', 'PTR', '0AF', 'TFG4', 'ESC', 'PRO']
  Fitness: 1.0000
  Total number of peptides: 16800
  Number of unique masses: 16800

Top 5 optimal schemes:

Scheme 1:
  Step 1: ['FVAL', 'TFG4', 'ABA', 'BIU', 'CTE', 'ACZ', 'AHB']
  Step 2: ['TYR', 'PHE', '4IN', 'HLU', '0BN', 'ASN', 'THR', 'Sep2', 'TYI', 'GLY']
  Step 3: ['NIY', 'BIF', 'MET', 'SER', 'THR', 'ARG']
  Step 4: ['CPH2', 'LEU', 'GGB', '2FM', 'MET']
  Step 5: ['CP24', 'PHI', 'DILE', 'PTR', '0AF', 'TFG4', 'ESC', 'PRO']
  Fitness: 1.0000
  Total number of peptides: 16800
  Number of unique masses: 16800

Scheme 2:
  Step 1: ['FVAL', 'TFG4',

In [ ]:
# @title Visualize
# @markdown Visualization module for Split Pool Scheme optimization results.

scheme_to_display = 1  # @param {type:"number"}
initial_scale = 0.1  # @param {type:"number"} {# Adjust this value to change the overall size of the spiral
scale_reducing_factor = 0.2 # @param {type:"number"} # Adjust this value to change how quickly the spiral contracts
class CombinatorialGraphGenerator:
    """Generates a combinatorial graph from a SplitPoolScheme."""

    @staticmethod
    def generate(scheme: SplitPoolScheme) -> nx.DiGraph:
        """Generate a combinatorial graph from the given scheme.

        Args:
            scheme: The SplitPoolScheme to visualize.

        Returns:
            A NetworkX DiGraph representing the combinatorial structure.
        """
        G = nx.DiGraph()
        root = 'Root'
        G.add_node(root, level=0, amino_acid='Root', mass=0, step=0)

        prev_level_nodes = [root]
        for level, step in enumerate(scheme.steps, start=1):
            current_level_nodes = []
            for prev_node in prev_level_nodes:
                for aa in step:
                    node_id = f"{prev_node}_{aa.name}"
                    G.add_node(node_id, level=level, is_d=aa.is_d, mass=aa.mass,
                               amino_acid=aa.name, step=level)
                    current_level_nodes.append(node_id)
                    G.add_edge(prev_node, node_id)
            prev_level_nodes = current_level_nodes

        return G

class GraphLayoutGenerator:
    """Generates layout for combinatorial graphs."""

    @staticmethod
    def spiral_layout(G: nx.DiGraph, root: str, steps: List[List[str]],
                      initial_scale: float, scale_reducing_factor: float) -> Dict[str, Tuple[float, float]]:
        """Generate a spiral layout for the graph.

        Args:
            G: The graph to layout.
            root: The root node of the graph.
            steps: The steps of the SplitPoolScheme.
            initial_scale: Initial scale factor for the spiral.
            scale_reducing_factor: Factor by which to reduce the scale at each step.

        Returns:
            A dictionary mapping node names to (x, y) coordinates.
        """
        def golden_ratio_spiral(n: int, scale: float) -> complex:
            golden_ratio = (1 + 5 ** 0.5) / 2
            theta = n * 2 * math.pi / golden_ratio
            r = scale * math.sqrt(n)
            return cmath.rect(r, theta)

        def layout_subtree(node: str, center: complex, scale: float, current_step: int = 0) -> None:
            pos[node] = (center.real, center.imag)

            if current_step >= len(steps):
                return

            children = [child for child in G.successors(node) if G.nodes[child]['step'] == current_step + 1]
            num_children = len(children)

            if num_children == 0:
                return

            child_scale = scale * scale_reducing_factor
            for i, child in enumerate(children):
                offset = golden_ratio_spiral(i+1, child_scale)
                child_pos = center + offset
                layout_subtree(child, child_pos, child_scale, current_step + 1)

        pos = {}
        layout_subtree(root, complex(0, 0), initial_scale)
        return pos

class MassCalculator:
    """Calculates total mass for nodes in the graph."""

    @staticmethod
    def calculate_total_mass(G: nx.DiGraph, node: str) -> float:
        """Calculate the total mass for a given node.

        Args:
            G: The graph containing the node.
            node: The node to calculate mass for.

        Returns:
            The total mass of the path from root to the given node.
        """
        total_mass = G.nodes[node]['mass']
        path = nx.shortest_path(G, source='Root', target=node)
        for n in path[1:-1]:  # Exclude root and the node itself
            total_mass += G.nodes[n]['mass']
        return total_mass

class GraphVisualizer:
    """Visualizes the combinatorial graph using Plotly."""

    def __init__(self, G: nx.DiGraph, pos: Dict[str, Tuple[float, float]],
                 scheme: SplitPoolScheme, scheme_index: int):
        self.G = G
        self.pos = pos
        self.scheme = scheme
        self.scheme_index = scheme_index

    def _prepare_edge_trace(self) -> go.Scatter:
        edge_x, edge_y = [], []
        for edge in self.G.edges():
            x0, y0 = self.pos[edge[0]]
            x1, y1 = self.pos[edge[1]]
            edge_x.extend([x0, x1, None])
            edge_y.extend([y0, y1, None])

        return go.Scatter(
            x=edge_x, y=edge_y,
            line=dict(width=0.5, color='#888'),
            hoverinfo='none',
            mode='lines')

    def _prepare_node_trace(self) -> go.Scatter:
        node_x, node_y = [], []
        node_colors, node_sizes, node_texts, mass_values = [], [], [], []
        terminal_nodes = [n for n in self.G.nodes() if self.G.out_degree(n) == 0]
        terminal_masses = [MassCalculator.calculate_total_mass(self.G, n) for n in terminal_nodes]
        mass_min, mass_max = min(terminal_masses), max(terminal_masses)

        for node in self.G.nodes():
            x, y = self.pos[node]
            node_x.append(x)
            node_y.append(y)

            if node in terminal_nodes:
                total_mass = MassCalculator.calculate_total_mass(self.G, node)
                mass_values.append(total_mass)
                node_colors.append(total_mass)
                node_sizes.append(10)
                node_texts.append(f"Node: {node}<br>Amino Acid: {self.G.nodes[node]['amino_acid']}<br>Total Mass: {total_mass:.2f}")
            else:
                mass_values.append(None)
                node_colors.append(mass_min - 1)
                node_sizes.append(10)
                node_texts.append(f"Node: {node}<br>Amino Acid: {self.G.nodes[node]['amino_acid']}")

        return go.Scatter(
            x=node_x, y=node_y,
            mode='markers+text',
            hoverinfo='text',
            marker=dict(
                showscale=True,
                colorscale='Viridis',
                reversescale=True,
                color=node_colors,
                size=node_sizes,
                colorbar=dict(
                    thickness=15,
                    title='Mass (Da)',
                    xanchor='left',
                    titleside='right'
                ),
                cmin=mass_min,
                cmax=mass_max,
                line_width=2),
            text=[self.G.nodes[node]['amino_acid'] for node in self.G.nodes()],
            textposition='middle center',
            textfont=dict(size=8),
            hovertext=node_texts)

    def visualize(self) -> None:
        """Create and display the visualization."""
        edge_trace = self._prepare_edge_trace()
        node_trace = self._prepare_node_trace()

        fig = go.Figure(data=[edge_trace, node_trace],
                        layout=go.Layout(
                            title=f'Interactive Peptide Library (Scheme {self.scheme_index + 1})',
                            titlefont_size=16,
                            showlegend=False,
                            hovermode='closest',
                            margin=dict(b=20,l=5,r=5,t=40),
                            annotations=[dict(
                                showarrow=False,
                                xref="paper", yref="paper",
                                x=0.005, y=-0.002)],
                            xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                            yaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                            width=600,
                            height=600,
                        ))

        fig.show()
        fig.write_html(f'/content/drive/MyDrive/Aa_Lokey_Lab/Unique Mass Genetic Library Generator/scheme_{self.scheme_index + 1}.html')

    def print_scheme_info(self) -> None:
        """Print additional information about the scheme."""
        print(f"\nScheme {self.scheme_index + 1}:")
        for j, step in enumerate(self.scheme.steps):
            print(f"  Step {j+1}: {[aa.name for aa in step]}")
        masses = self.scheme.masses
        terminal_nodes = [n for n in self.G.nodes() if self.G.out_degree(n) == 0]
        terminal_masses = [MassCalculator.calculate_total_mass(self.G, n) for n in terminal_nodes]
        print(f"  Total number of peptides: {len(masses)}")
        print(f"  Number of unique masses: {len(set(masses))}")
        print(f"  Mass range: {min(terminal_masses):.2f} - {max(terminal_masses):.2f} Da")
        print(f"  Total nodes in graph: {self.G.number_of_nodes()}")

def visualize_scheme(scheme: SplitPoolScheme, scheme_index: int, initial_scale: float, scale_reducing_factor: float) -> None:
    """Visualize a single SplitPoolScheme.

    Args:
        scheme: The SplitPoolScheme to visualize.
        scheme_index: The index of the scheme (for labeling purposes).
        initial_scale: Initial scale factor for the spiral layout.
        scale_reducing_factor: Factor by which to reduce the scale at each step.
    """
    G = CombinatorialGraphGenerator.generate(scheme)
    steps = [[aa.name for aa in step] for step in scheme.steps]
    pos = GraphLayoutGenerator.spiral_layout(G, root='Root', steps=steps,
                                             initial_scale=initial_scale,
                                             scale_reducing_factor=scale_reducing_factor)
    visualizer = GraphVisualizer(G, pos, scheme, scheme_index)
    visualizer.visualize()
    visualizer.print_scheme_info()

optimal_scheme = optimal_schemes[scheme_to_display - 1]
visualize_scheme(optimal_scheme, scheme_to_display - 1, initial_scale, scale_reducing_factor)


Scheme 1:
  Step 1: ['FVAL', 'TFG4', 'ABA', 'BIU', 'CTE', 'ACZ', 'AHB']
  Step 2: ['TYR', 'PHE', '4IN', 'HLU', '0BN', 'ASN', 'THR', 'Sep2', 'TYI', 'GLY']
  Step 3: ['NIY', 'BIF', 'MET', 'SER', 'THR', 'ARG']
  Step 4: ['CPH2', 'LEU', 'GGB', '2FM', 'MET']
  Step 5: ['CP24', 'PHI', 'DILE', 'PTR', '0AF', 'TFG4', 'ESC', 'PRO']
  Total number of peptides: 16800
  Number of unique masses: 16800
  Mass range: 425.74 - 1080.15 Da
  Total nodes in graph: 19398


# Clean Amino Acid Library and Compute Mass

In [ ]:
# @title Fix Scraped Data

"""
def clean_and_combine_csv(input_file, output_file):
    # Read the CSV file
    df = pd.read_csv(input_file)

    # Create separate dataframes for each column
    df_id = df[['id_d_form']].dropna()
    df_name = df[['full_name']].dropna()
    df_smi = df[['smi-href']].dropna()

    # Reset indices for each dataframe
    df_id = df_id.reset_index(drop=True)
    df_name = df_name.reset_index(drop=True)
    df_smi = df_smi.reset_index(drop=True)

    # Determine the maximum length
    max_length = max(len(df_id), len(df_name), len(df_smi))

    # Pad shorter dataframes with NaN values
    df_id = df_id.reindex(range(max_length), fill_value=pd.NA)
    df_name = df_name.reindex(range(max_length), fill_value=pd.NA)
    df_smi = df_smi.reindex(range(max_length), fill_value=pd.NA)

    # Combine the dataframes
    combined_df = pd.concat([df_id, df_name, df_smi], axis=1)

    # Replace NaN values with empty strings
    combined_df = combined_df.fillna('')

    # Rename "smi-href" to "smi_href"
    combined_df.rename(columns={'smi-href': 'smi_href'}, inplace=True)

    # Write the combined data to a new CSV file
    combined_df.to_csv(output_file, index=False)

    print(f"Total rows in output: {len(combined_df)}")

# Usage
input_file = '/content/drive/MyDrive/Aa_Lokey_Lab/Unique Mass Library Generator/swiss_sidechain_broken.csv'
output_file = '/content/drive/MyDrive/Aa_Lokey_Lab/Unique Mass Library Generator/swiss_sidechain.csv'

clean_and_combine_csv(input_file, output_file)
"""

In [ ]:
# @title Fetch SMILES and Compute Mass
"""
def fetch_smi_content(url):
    response = requests.get(url)
    if response.status_code == 200:
        return response.text.strip().split("\t")[0]
    else:
        return None

def parse_smiles(smi):
    atomic_masses = {
        'H': 1.008, 'C': 12.011, 'N': 14.007, 'O': 15.999, 'F': 18.998,
        'P': 30.974, 'S': 32.065, 'Cl': 35.453, 'Br': 79.904, 'I': 126.904
    }

    pattern = r'(\[([A-Z][a-z]?)([+-]?\d*)\]|([A-Z][a-z]?))(\d*)'

    atom_counts = {}

    for match in re.findall(pattern, smi):
        if match[1]:  # Bracketed atom
            atom = match[1]
            count = int(match[4]) if match[4] else 1
        else:  # Non-bracketed atom
            atom = match[3]
            count = int(match[4]) if match[4] else 1

        atom_counts[atom] = atom_counts.get(atom, 0) + count

    total_mass = sum(atomic_masses.get(atom, 0) * count for atom, count in atom_counts.items())

    return total_mass, atom_counts

def calculate_mass(smi):
    # Change [NH3] to [NH2]
    smi = smi
    mass, atom_counts = parse_smiles(smi)
    return mass

# Load the dataframe
df = sidechains

df['mass'] = None
df['smiles'] = None

# Iterate through the rows
for index, row in tqdm(df.iterrows()):
    smi_url = row['smi_href']
    smi_content = fetch_smi_content(smi_url).replace('[NH3]', '[NH2]')

    if smi_content:
        mass = calculate_mass(smi_content)
        df.at[index, 'mass'] = mass
        df.at[index, 'smiles'] = smi_content


df.to_csv('/content/drive/MyDrive/Aa_Lokey_Lab/Unique Mass Library Generator/swiss_sidechain.csv', index=False)
"""